Connect to EODC Dask


Authenticating and connecting to EODC Dask can be done with a few lines of Python code.


Run the following in order to make sure all dependencies are met.


In [1]:
from eodc.dask import EODCDaskGateway
from rich.console import Console
from rich.prompt import Prompt


In [7]:
console = Console()
your_username = Prompt.ask(prompt="Enter your Username")
gateway = EODCDaskGateway(username=your_username)


Enter your Username:

Unclosed client session
client_session: <aiohttp.client.ClientSession object at 0x7cbe4dbebc40>


In [3]:
#Change Cluster configuration if needed
cluster_options = gateway.cluster_options()
cluster_options


Options<worker_cores=2,
        worker_memory=2.0,
        image='registry.eodc.eu/eodc/clusters/dedl-deployment/dedl-dask:2023.08.3'>


Create a Dask Cluster
Now we are going to create a Dask Cluster in order to run compute jobs. To communicate with the cluster we have to instantiate a client as well. Per default, no worker nodes are spawned, but this can be done either manually or even by enabling adaptive scaling of the cluster.

Important: Please use the widget to add/scale the Dask workers. Per default no worker is spawned, therefore no computations can be performed by the cluster.


In [4]:
cluster =gateway.new_cluster(cluster_options)

In [9]:

#cluster = gateway.new_cluster(cluster_options)
client = cluster.get_client()
cluster


If you want to spawn a workers directly via Python adaptively please use the following method call. With the following the cluster will be scaled to 2 workers initially. Depending on the load, Dask will add addtional workers, up to 5, if needed.


In [10]:

cluster.adapt(minimum=2, maximum=5)
#List clusters if available
console.print(gateway.list_clusters())


KeyError: 'refresh_token'

We can connect to already running clusters again.


In [11]:

cluster = gateway.connect(gateway.list_clusters()[0].name)
console.print(cluster)


GatewayCluster<dask-gateway.98714cbf1bc5495480e3df49da2f977e, status=running>

Display Dask Dashboard to monitor execution of computations
Copy the following link into a browser of your choice. Please consider the dashboard url provided is making use of http and not https.


In [19]:

cluster.dashboard_link

'http://dask.dev.services.eodc.eu/clusters/dask-gateway.98714cbf1bc5495480e3df49da2f977e/status'

In [ ]:
cluster.

## flood map

In [13]:
import pystac_client
from odc import stac as odc_stac
import xarray as xr
import rioxarray
import numpy as np
#import hvplot.xarray
import zipfile
from pathlib import Path
import shutil

In [14]:
chunks = {'time':1, "latitude": 1300, "longitude": 1300}
crs = "EPSG:4326" # Coordinate Reference System - World Geodetic System 1984 (WGS84) in this case 
res = 0.00018 # 20 meter in degree
time_range = "2022-10-11/2022-10-25"
minlon, maxlon = 12.3, 13.1
minlat, maxlat = 54.3, 54.6
bounding_box = [minlon, minlat, maxlon, maxlat]
eodc_catalog = pystac_client.Client.open("https://stac.eodc.eu/api/v1")

In [15]:
search = eodc_catalog.search(
    collections="SENTINEL1_SIG0_20M",
    bbox=bounding_box,
    datetime=time_range,
)

items_sig0 = search.item_collection()
items_sig0

In [16]:
def extract_orbit_names(items):
    return np.array([items[i].properties["sat:orbit_state"][0].upper() + \
                     str(items[i].properties["sat:relative_orbit"]) \
                     for i in range(len(items))])

def post_process_eodc_cube(dc: xr.Dataset, items, bands):
    if not isinstance(bands, tuple):
        bands = tuple([bands])
    for i in bands:
        dc[i] = post_process_eodc_cube_(dc[i], items, i)#https://github.com/TUW-GEO/dask-flood-mapper.git
    return dc

def post_process_eodc_cube_(dc: xr.Dataset, items, band):
    scale = items[0].assets[band].extra_fields.get('raster:bands')[0]['scale']
    nodata = items[0].assets[band].extra_fields.get('raster:bands')[0]['nodata']
    return dc.where(dc != nodata) / scale

bands = "VV"
sig0_dc = odc_stac.load(items_sig0,
                        bands=bands,
                        crs=crs,
                        chunks=chunks,
                        resolution=res,
                        bbox=bounding_box,
                        resampling="bilinear",
                        groupby=None,
                        )

In [17]:
sig0_dc = post_process_eodc_cube(sig0_dc, items_sig0, bands).\
    rename_vars({ "VV": "sig0"}).\
    assign_coords(orbit=("time", extract_orbit_names(items_sig0))).\
    dropna(dim="time", how="all").\
    sortby("time")

RuntimeError: Error during deserialization of the task graph. This frequently occurs if the Scheduler and Client have different environments. For more information, see https://docs.dask.org/en/stable/deployment-considerations.html#consistent-software-environments


In [18]:
from dask.distributed import get_worker
import dask
print(get_worker().dask_version)


ValueError: No worker found

In [ ]:
from dask.distributed import PipInstall

plugin = PipInstall(packages=["odc"])#, pip_options=["--upgrade"])

#client.register_plugin(plugin)

In [ ]:
sig0_dc_ = client.compute(sig0_dc, sync=True)

In [ ]:
import coiled

clustercoiled = coiled.Cluster(
    n_workers=15,  # Coiled automatically syncs packages by default
)
client = cluster.get_client()

In [3]:
cluster.close(shutdown=True)

NameError: name 'cluster' is not defined

In [ ]:
import dask.array as da
x = da.ones((10,10), chunks=(1, 1))
x.sum().compute()
